# Kernel density estimation for dyadic data
_Bryan Graham - University of California - Berkeley_  
_Fengshi Niu - University of California - Berkeley_  
_James Powell - University of California - Berkeley_  

June 2019

This notebook replicates the Monte Carlo experiments reported in the paper _Kernel Density Estimation for Undirected Dyadic Data_. While that paper only studies the case of undirected data, the **dyadic_kden()** function introduced below can handle both directed and undirected data (the former of which is a topic of ongoing research.
<br>
<br>
Please feel free to use and adapt this code for your own projects. We ask only that you cite our paper and the use of this codebase.
<br>
<br>
This code is provided "as is" without implicit warranty. While we welcome bug reports or suggestions for improvements, we regret that we are not able to provide any support. You are on your own!

#### Code citation:
<br>
Graham, Bryan S., Niu, Fengshi and Powell James. (2019). "Kernel density estimation for dyadic data: Python Jupyter Notebook," (Version 1.0) [Computer program]. Available at http://bryangraham.github.io/econometrics/ (Accessed 18 March 2020)
<br>
<br>
Graham, Bryan S., Niu, Fengshi and Powell James. (2019). "Kernel density estimation for undirected dyadic data" [Working Paper]. Available at http://bryangraham.github.io/econometrics/ (Accessed 18 March 2020)

In [1]:
# Direct Python to plot all figures inline (i.e., not in a separate window)
%matplotlib inline

# Main scientific computing modules
# Load library dependencies
import time
import numpy as np
import scipy as sp
import scipy.stats
import pandas as pd
import itertools as it
import math as math

# Import matplotlib 
import matplotlib.pyplot as plt
import seaborn as sns

# networkx module for the analysis of network data
import networkx as nx

Directory where graphics files will be saved.

In [2]:
graphics     = '/Users/bgraham/Dropbox/Research/Networks/DyadicRegression/Graphics/'

# Dyadic Density Estimation

This first block of code defines the **dyadic_kden()** function. It currently only supports one dimensional density estimation problems, but it can handle both undirected and directed data. It includes various options to plot your density estimate along with pointwise confidence bands. The main input to the function is a vector of dyadic outcomes. This vector must be a Panda series  object with a multi-index (see documentation in the function below).

In [3]:
def dyadic_kden(X, x_grid, h = None, smooth_factor = 1, directed = True, cov='DR_bc', spike = False, plot = False):
    
    """
    AUTHOR: Bryan S. Graham, UC - Berkeley, bgraham@econ.berkeley.edu, January 2019
    PYTHON 3.6 (Updated May 2019)
    
    This function computes dyadic kernel density estimates. A variety of standard error estimates, 
    as described further below, are available to be reported along with point estimates of the density 
    function. The estimator, as well as its theoretical properties, are described in 
    Graham, Niu and Powell (2019,"Kernel density estimation for dyadic data").
        
    N = number of agents
    n = N(N-1), the number of *directed* dyads, or n = 0.5N(N-1), the number of *undirected* dyads
    
    
    INPUTS:
    -------
    X              :  n-length Pandas series with outcome for each
                      (directed) dyad as elements (needs to have MultiIndex)
    x_grid         :  m x 1 grid of values at which to estimate f(x) (also a Pandas series) 
    h              :  Bandwidth (scalar); if none use Silverman's rule-of-thumb
    smooth_factor  :  Blow-up or scale-down bandwidth by a multiplicative factor
    directed       :  if True then assume N*(N-1) directed outcomes present, 
                      otherwise assume 0.5*N(N-1) undirected outcomes are present
    cov            :  covariance matrix estimator - 
                      'ind', 'DR', 'DR_bc' are allowable choices (see below)
    spike          :  If True then f(x) is assumed to be defined on positive part of real line
                      with a (possible) spike at zero. If Spike == True the user should exclude
                      x=0 from the x_grid. The program will then renormalize the estimated density
                      to integrate to Pr(X>0) and separately estimate the mass point Pr(X=0)
    plot           :  If True, then plot density estimate and confidence band                  
    
    
    The three variance-covariance matrices are as described in Graham (forthcoming, 
    Handbook of Econometrics). 'ind' assumes independence across dyads (note this 
    corresponds to "clustering" on dyads in the directed case where each dyad is 
    observed twice); `DR' allows for dependence across dyads sharing an agent in 
    common. It corresponds to the usual Jackknife variance estimate of the leading 
    term in the asymptotic variance expression. 'DR_bc' is a bias-corrected variance estimate.
    This estimate also includes "higher order" variance components.
    
    
    OUTPUTS:
    --------
    f_hat        : m x 1 vector of regression function estimates 
    vcov_f_hat   : m x m variance-covariance matrix 
    fig          : matlibplot figure object
    Sigma1_bc    : bias-corrected estimate of Sigma1 (m vector)
    Sigma2       : estimated of Sigma2 (m vector)
    
    """
    
    #-------------------------------------------------------------------#
    #- STEP 1 : ORGANIZE DATA AND PREPARE FOR ESTIMATION               -#
    #-------------------------------------------------------------------#
    
    # Check to make sure X is a pandas objects with multi-indices
    if not isinstance(X.index, pd.core.index.MultiIndex):
        print("X is not a Pandas Series with an (i,j) multi-index")
        return [None, None, None]
    
    # Get dataset dimensions and agent/dyad indices
    n        = len(X)               # Number of directed/undirected dyads (n = N(N-1) or 0.5N(N-1))
    i, j     = X.index.levels       # Agent-level indices associated with each dyad
    agents   = set(i | j)           # Set of all unique agent-level indices (N elements)
    N        = len(agents)          # Number of agents    
    idx, jdx = list(X.index.names)  # Labels for i and j indices (e.g., 'exporter', 'importer')
    
    # Check to see if expected number of outcomes are present. Function
    # only works with balanced datasets at the present time.
    if directed and (n != N*(N-1)):
        print("Number of directed outcomes does not equal N(N-1)")
        return [None, None, None]
        
    if not directed and (n != (N*(N-1) // 2)):
        print("Number of undirected outcomes does not equal N(N-1)/2")    
        return [None, None, None]
    
    # Set bandwidth value if needed (Silverman's rule-of-thumb)
    if h is None:
        iqr   = np.subtract.reduce(np.percentile(X, [75,25]))  # inter-quartile range, returned as scalar
        sigma = np.std(X, ddof=1)                              # standard deviation
        A     = min(sigma, iqr/1.349)                          # pick smallest of two dispersion measures
        h     = smooth_factor * 0.9 * A * n ** (-1/5.)         # Silverman's rule-of-thumb times additional
                                                               # user-supplied "smooth factor"

    #-------------------------------------------------------------------#
    #- STEP 2 : COMPUTE KERNEL DENSITY ESTIMATES                       -#
    #-------------------------------------------------------------------#
       
    # Sort data prior to estimation (speeds up variance-covariance calculation)
    X.sort_index(level = [idx, jdx], inplace = True) 
    
    # Initialize density estimate objects
    m      = len(x_grid)               # number of grid points at which density is being estimates
    k      = np.zeros((n,m))           # n x m matrix of kernel values
    S_ij   = np.zeros((n,m))           # "score" values
    f_hat  = np.zeros((m,))            # m-vector of density estimates
    
    for l in range(0,m):
        x_l       = x_grid.iloc[[l]].values - X.values             # n x 1 vector of X_ij - x values
        k[:,l]    = sp.stats.norm.pdf(x_l/h)/h                     # n x 1 vector of k((x - X_ij)/h) values
        S_ij[:,l] = k[:,l]                                         # Summands of estimator
        f_hat[l]  = np.mean(S_ij[:,l])                             # Kernel estimate of f(x)
        S_ij[:,l] = (k[:,l] - f_hat[l])                            # Re-center n x 1 S_ij vector to be mean zero
        
    
    #-------------------------------------------------------------------#
    #- STEP 3 : COMPUTE VARIANCE-COVARIANCE MATRIX                     -#
    #-------------------------------------------------------------------#
       
    if not directed:
        
        #-----------------------------------#
        #- Case 1: Undirected outcome data -#
        #-----------------------------------#
        
        # Compute estimates of Sigma1 and Sigma2, the covariance between "score"
        # contributions with, respectively, one and two indices in common. 
        
        s_bar2 = S_ij                    # s_bar2 is the same as S_ij calculate above (n x m)
        s_bar1 = np.zeros((N,m))         # Initialize matrix for score Hajek projections                          
        lt_ij  = np.tril_indices(N,-1)   # Indices of lower triangle of an N x N matrix      
        
        # Form scores and projection using S_ij 
        for l in range(0,m):
            S_l_ij         = np.zeros((N,N))                                  # Form N x N symmetric matrix with
            S_l_ij[lt_ij]  = s_bar2[:,l]                                      # s_bar2 "scores" as elements
            S_l_sym        = (S_l_ij + S_l_ij.T)                              # Mirror lower triangle in upper triangle
            s_bar1[:,l]    = (N/(N-1))*np.mean((S_l_sym + S_l_sym.T), axis=0) # Column sums of symmetric N x N matrix with scores
                                                                              # (Hajek projection terms)
        
        # Compute Sigma2 (summation over N choose 2 terms)
        Sigma2 = (s_bar2[:,l].reshape(-1,1).T @ s_bar2[:,l].reshape(-1,1))/n  # m x m
        Sigma2 = np.diag(np.diag(Sigma2))                                     # m vector
         
        # Compute Sigma1 (summation over N terms)
        Sigma1 = (s_bar1.T @ s_bar1)/N                                        # m x m
        Sigma1 = np.diag(np.diag(Sigma1))                                     # m vector
    
    else:
        #-----------------------------------#
        #- Case 2: Directed outcome data   -#
        #-----------------------------------#
        
        # Compute estimates of Sigma1 and Sigma2, the covariance between "score"
        # contributions with, respectively, one and two indices in common. In
        # the directed case we first need to symmetrize the score prior
        # to the required U-statistic type variance calculations.
        # Combine S_ij + S_ji to form symmetrized kernel "s_bar2"    
        
        s_bar2 = np.zeros((n // 2,m))    # Initialize matrix for symmetrized scores
        s_bar1 = np.zeros((N,m))         # Initialize matrix for score projections
        lt_ij  = np.tril_indices(N,-1)   # Indices of lower triangle of an N x N matrix 
        
        # Form symmetrized scores using S_ij (non-symmetric "Scores")
        for l in range(0,m):
            S_l         = S_ij[:,l].reshape(((N-1),N), order="F")           # reshape N(N-1) x 1 score into N-1 x N matrix
            S_l_ij      = np.vstack([np.zeros((N,)),np.tril(S_l, k=0)])     # pad and rotate to compute S_ij + S_ji for 
            S_l_ji      = np.vstack([np.triu(S_l, k=1), np.zeros((N,))])    # all 0.5N(N-1) dyads
            S_l_sym     = (S_l_ij + S_l_ji.T)/2                             # Lower triangle matrix with symmetric kernels
            s_bar2[:,l] = S_l_sym[lt_ij]                                    # 0.5N(N-1) x 1 vector of symmetric scores for theta_k
            s_bar1[:,l] = (N/(N-1))*np.mean((S_l_sym + S_l_sym.T), axis=0)  # Column sums of symmetric N x N matrix with scores
                                                                            # (Hajek projection terms)
        
        # Compute Sigma2 (summation over N choose 2 terms)
        Sigma2 = 2*(s_bar2.T @ s_bar2)/n                                   # m x m
        Sigma2 = np.diag(np.diag(Sigma2)) 
         
        # Compute Sigma1 (summation over N terms)
        Sigma1 = (s_bar1.T @ s_bar1)/N                                     # m x m
        Sigma1 = np.diag(np.diag(Sigma1)) 
      
    # Bias correct estimate of Sigma1 as in Efron/Stein 
    # Sigma1 = ((N-1)/(N-2))*(Sigma1 - Sigma2/(N-1))
    
    # Compute the asymptotic variance-covariance matrix 
    # according to specificed method
    
    if cov == 'ind':
        # Assume independence across dyads
        vcov_f_hat = (2/(N-1))*(Sigma2)/N
    elif cov == 'DR':
        # Dependence across dyads allowed, only leading variance term retained
        vcov_f_hat = 4*(Sigma1)/N
    else:
        # Dependence across dyads allowed, both variance terms retained
        vcov_f_hat = 4*((Sigma1 - 0.5*Sigma2/(N-1)))/N
        
        # Use eigendecomposition to ensure variance matrix is positive
        # definite
        [L, Q] = np.linalg.eig(vcov_f_hat)
        if not np.all(L>0):               # check for negative eigenvalues
            L[L<0] = 0                    # remove negative eigenvalues
            L      = np.diag(L)
            iQ     = np.linalg.inv(Q)
            vcov_f_hat = Q @ L @ iQ       # positive definite matrix
    
    # Form bias-corrected estimates of Sigma1 variance term
    # (useful for Monte Carlo analysis and other comparisons)
    Sigma1_bc = ((N-1)/(N-2))*(Sigma1 - Sigma2/(N-1))
        
    #-------------------------------------------------------------------#
    #- STEP 4 : PLOT DENSITY ESTIMATE WITH POINTWISE CONFIDENCE BAND   -#
    #-------------------------------------------------------------------#
    
    if plot:
        
        # Compute pointwise 95 percent confidence band
        l_cib = f_hat - 1.96*np.sqrt(np.diag(vcov_f_hat))
        u_cib = f_hat + 1.96*np.sqrt(np.diag(vcov_f_hat))
        
        fig, ax = plt.subplots(nrows=1, ncols=1, figsize=(9, 6))
        plt.sca(ax)  

        # Adjust for spike at zero if relevant
        if spike:
            fraction_positive = np.count_nonzero(X)/(N*(N-1))
            f_hat = f_hat*fraction_positive
            l_cib = l_cib*fraction_positive
            u_cib = u_cib*fraction_positive
            plt.xlim([-0.1, x_grid.iloc[:].max()])     # plot mass at zero & rescale density 
            plt.ylim([x_grid.iloc[:].min(), \
                      np.max(u_cib) + 0.1*np.abs(np.max(u_cib))])
            ax2 = ax.twinx()                           # instantiate a second axes that shares the same x-axis
            ax2.set_ylabel('Mass at zero, ' + r'$\Pr\left(X=0\right)$', fontsize=16)
            ax2.axvline(x=0, ymin=0, ymax=1-fraction_positive, color = '#ED4E33', linewidth = 10, alpha=0.3) 
        else:
            plt.xlim([x_grid.iloc[:].min(), x_grid.iloc[:].max()])
            plt.ylim([0, \
                      np.max(u_cib) + 0.1*np.abs(np.max(u_cib))])
        
        ax.plot(x_grid, f_hat, color = '#FDB515', linewidth = 2)
        ax.plot(x_grid, l_cib, color = '#003262', linewidth = 2, linestyle='dashed')
        ax.plot(x_grid, u_cib, color = '#003262', linewidth = 2, linestyle='dashed')

        ax.fill_between(x_grid.iloc[:], l_cib,  u_cib,  facecolor='#003262', alpha=0.2)
        ax.fill_between(x_grid.iloc[:], f_hat,          facecolor='#FDB515', alpha=0.2)
                    
        # Add title and axis labels
        from matplotlib import rc
        rc('text', usetex=True)
        plt.title('Kernel Density Estimate', fontsize=16)
        ax.set_xlabel(X.name + ', x', fontsize=16)
        ax.set_ylabel('Density, ' + r'$f(x)$', fontsize=16)
        
        # Clean up the plot, add frames etc.
        ax.patch.set_facecolor('#DDD5C7')            # Color of background
        ax.patch.set_alpha(0.35)                     # Translucency of background
        ax.grid(False)                               # Remove gridlines from plot

        # Add frame around plot
        for spine in ['left','right','top','bottom']:
            ax.spines[spine].set_visible(True)
            ax.spines[spine].set_color('k')
            ax.spines[spine].set_linewidth(2)
    else:
        fig = None
            
    return [f_hat, vcov_f_hat, fig, Sigma1_bc, Sigma2]            

# Monte Carlo Experiments

This next block of code executes a small Monte Carlo experiment. For each Monte Carlo replication, a total $ n=\binom{N}{2} $ outcomes of the form $Y_{ij}=A_{i}A_{j}+V_{ij} $ are generated. Here the $\left\{ A_{i}\right\} _{i=1}^{N}$ are iid random variables which equal -1 with probability $q$ and 1 with probability $1-q$. The  $\left\{ V_{ij}\right\} _{i<j}$ are i.i.d. standard normal.
<br>
<br>
We estimate $f_{Y}(1.645)$. We check the coverage properties of confidence intervals which ignore the presence of dependence across dyads sharing an agent in common as well as those constructed using the variance estimator proposed in the paper (which does take into account dyadic dependence).
<br>
<br>
For the bandwidth we use the MSE-optimal one derived in the Graham, Niu and Powell (2019). This is an oracle bandwidth choice and not feasible (of course) in practice.
<br>
<br>
We begin with some "pencil and paper" calculations which summarize the main features of our Monte Carlo designs.

In [4]:
R2 = 1/(2*np.sqrt(math.pi))
K2 = 1

q = 1/3
w = 1.645

f_Am1 = q*sp.stats.norm.pdf(w-1) + (1-q)*sp.stats.norm.pdf(w+1)
f_Ap1 = q*sp.stats.norm.pdf(w+1) + (1-q)*sp.stats.norm.pdf(w-1)
f_0 = (q**2 + (1-q)**2)*sp.stats.norm.pdf(w-1) + 2*q*(1-q)*sp.stats.norm.pdf(w+1)
D2f = (q**2 + (1-q)**2)*((w-1)**2-1)*sp.stats.norm.pdf(w-1) + 2*q*(1-q)**((w+1)**2-1)*sp.stats.norm.pdf(w+1)
B = 0.5*D2f*K2

OMEGA1 = q*f_Am1**2 + (1-q)*f_Ap1**2 - f_0**2
OMEGA2 = f_0*R2

sample_sizes = [100, 400, 1600]

bandwidths = []

for N in sample_sizes:
    
    n      = N*(N-1) // 2
    h_opt  = (0.25*(OMEGA2/B**2)*(1/n))**(1/5)
        
    if N != 100:
        h_alt = bandwidths[0][0]*((sample_sizes[0]*(sample_sizes[0]-1) // 2)**(1/5))*(1/N)
        bw     = [h_opt, h_alt]
    else:
        bw     = [h_opt]
    
    bandwidths.append(bw)
    
    print("----------------------------------------")
    print("N = " + '{0:.0f}'.format(N))
    print("f(w):       " + '{0:.8f}'.format(f_0))
    
    for h in bw:
        print("Bandwidth:  " + '{0:.8f}'.format(h))
        print("Bias:       " + '{0:.8f}'.format((h**2)*B))
        print("ase:        " + '{0:.8f}'.format(np.sqrt(2*OMEGA1*(N-2)/n + OMEGA2/(n*h))))
        print("stddev, T1: " + '{0:.8f}'.format(np.sqrt(2*OMEGA1*(N-2)/n)))
        print("stddev, T3: " + '{0:.8f}'.format(np.sqrt(OMEGA2/(n*h))))
        print("")

----------------------------------------
N = 100
f(w):       0.18537581
Bandwidth:  0.24961154
Bias:       -0.00325281
ase:        0.01172446
stddev, T1: 0.00975396
stddev, T3: 0.00650563

----------------------------------------
N = 400
f(w):       0.18537581
Bandwidth:  0.14314795
Bias:       -0.00106979
ase:        0.00534278
stddev, T1: 0.00489565
stddev, T3: 0.00213959

Bandwidth:  0.00342078
Bias:       -0.00000061
ase:        0.01468107
stddev, T1: 0.00489565
stddev, T3: 0.01384075

----------------------------------------
N = 1600
f(w):       0.18537581
Bandwidth:  0.08218603
Bias:       -0.00035264
ase:        0.00254962
stddev, T1: 0.00245013
stddev, T3: 0.00070527

Bandwidth:  0.00085520
Bias:       -0.00000004
ase:        0.00733518
stddev, T1: 0.00245013
stddev, T3: 0.00691388



We perform 1000 Monte Carlo simulations for $N=100,400$ and $1,600$. The paper summarizes these experiments, but the main gist is that the theory does a pretty good job of approximating finite sample behavior.

In [20]:
# number of Monte Carlo replications
B      = 1000

# set random seed
np.random.seed(361)

design = 0

for N in sample_sizes:
    
    num_h = len(bandwidths[design])                # number of bandwidths for current design
    Simulation_Results = np.zeros((B,7*num_h))     # matrix to store results in form current design
    
    
    # ------------------------------------ #
    # PERFORM B MONTE CARLO REPLICATIONS - #
    # ------------------------------------ #

    for b in range(0,B):
        
        # Start timer
        start = time.time()

        # Generate simulated sample
        A = -1 + 2*(np.random.uniform(0,1,N)>=q)
        Y = []

        for i, j in it.combinations(range(0,N), 2):
            Y.append([A[i]*A[j] + np.random.normal(0, 1), i, j])
    
        Y = pd.DataFrame(Y, columns=['Y', 'i', 'j'])    
        Y = Y.set_index(['i', 'j'], drop = True)  # Set dataframe multi-index
        Y = Y.iloc[:,0]
        
        i = 0

        for bw in bandwidths[design]:
        
            try:
                # compute kernel density estimate, confidence intervals etc.
                [f_hat, vcov_hat, _, Sigma1_bc, Sigma2] = dyadic_kden(Y, pd.Series([w]), h = bw, smooth_factor = 1, \
                                                                      directed = False, cov='DR_bc', spike=False, plot = False)
         
                Simulation_Results[b,i*7 + 0] = True
                Simulation_Results[b,i*7 + 1] = f_hat[0] - f_0                     # Record bias of density estimate
                Simulation_Results[b,i*7 + 2] = vcov_hat[0,0]**(1/2)               # Record standard error estimate (FG)
            
                # Check coverage of 95 percent Wald asymptotic confidence interval (ignoring dyadic dependence)
                Simulation_Results[b,i*7 + 3] = (f_hat[0] - 1.96*((2/(N-1))*(Sigma2)/N)**(1/2) <= f_0) & \
                                                (f_hat[0] + 1.96*((2/(N-1))*(Sigma2)/N)**(1/2) >= f_0)
            
                # Check coverage of 95 percent Wald asymptotic confidence interval (accounting for dyadic dependence)
                Simulation_Results[b,i*7 + 4] = (f_hat[0] - 1.96*(4*Sigma1_bc[0,0]/N)**(1/2) <= f_0) & \
                                                (f_hat[0] + 1.96*(4*Sigma1_bc[0,0]/N)**(1/2) >= f_0)
            
                # Check coverage of 95 percent Wald asymptotic confidence interval (FG standard errors)
                Simulation_Results[b,i*7 + 5] = (f_hat[0] - 1.96*Simulation_Results[b,i*7 + 2] <= f_0) & \
                                                (f_hat[0] + 1.96*Simulation_Results[b,i*7 + 2] >= f_0)
            
                # Squared error loss
                Simulation_Results[b,i*7 + 6] = (f_hat[0]-f_0)**2
        
            except:        
                Simulation_Results[b,i*7 + 0] = False
            
            i += 1
            
        end = time.time()
        if (b+1) % 50 == 0:
            print("N = "+ str(N)+", Time required f/ MC rep  " + \
                  str(b+1) + " of " + str(B) + ": " + str(end-start))          
                     
    # ------------------------------------------------ #
    # - SUMMARIZE RESULTS OF MONTE CARLO EXPERIMENT  - #
    # ------------------------------------------------ #
    
    print("------------------------------------")
    print("RESULTS FOR N = " + str(N)) 
    print("------------------------------------")
    print("")
    
    i = 0
    
    for bw in bandwidths[design]:
        print("Bandwidth:  " + '{0:.8f}'.format(h))
        print("Number of times kernel estimate of the density was successfully computed")
        print(np.sum(Simulation_Results[:,0], axis = 0)) 
                      
        # find simulation replicates where computation was successful
        b = np.where(Simulation_Results[:,i*7 + 0])[0]
        SimRes = Simulation_Results[b,:]
                      
        # create Pandas dataframe with Monte Carlo results
        SR=pd.DataFrame({'Bias'           :  SimRes[:,i*7 + 1], 'StdErr'         :  SimRes[:,i*7 + 2],\
                         'Coverage (ind)' :  SimRes[:,i*7 + 3], 'Coverage (1st)' :  SimRes[:,i*7 + 4],
                         'Coverage (FG)'  :  SimRes[:,i*7 + 5], 'Squared Error'  :  SimRes[:,i*7 + 6]})                      

        print("")
        print("Monte Carlo summary statistics for density estimation")
        print("")
        print(SR.describe())

        print("")
        print('Root mean squared error (RMSE) of density estimate')
        print((SR['Squared Error'].mean())**(1/2))
        print("")
        
        Q = SR[['Bias']].quantile(q=[0.05,0.95])
        print("")
        print('Robust estimate of standard deviation of density estimate')
        print((Q['Bias'][0.95]-Q['Bias'][0.05])/(2*1.645)) 
        print("")
            
        i += 1
    
    design += 1
        

N = 100, Time required f/ MC rep  50 of 1000: 0.031723976135253906
N = 100, Time required f/ MC rep  100 of 1000: 0.028885841369628906
N = 100, Time required f/ MC rep  150 of 1000: 0.028673171997070312
N = 100, Time required f/ MC rep  200 of 1000: 0.02912306785583496
N = 100, Time required f/ MC rep  250 of 1000: 0.027776002883911133
N = 100, Time required f/ MC rep  300 of 1000: 0.028100967407226562
N = 100, Time required f/ MC rep  350 of 1000: 0.0365910530090332
N = 100, Time required f/ MC rep  400 of 1000: 0.02780294418334961
N = 100, Time required f/ MC rep  450 of 1000: 0.027915000915527344
N = 100, Time required f/ MC rep  500 of 1000: 0.027637004852294922
N = 100, Time required f/ MC rep  550 of 1000: 0.03133797645568848
N = 100, Time required f/ MC rep  600 of 1000: 0.03060770034790039
N = 100, Time required f/ MC rep  650 of 1000: 0.028181076049804688
N = 100, Time required f/ MC rep  700 of 1000: 0.032354116439819336
N = 100, Time required f/ MC rep  750 of 1000: 0.071723

In [5]:
# This imports an attractive notebook style from Github
from IPython.display import HTML
from urllib.request import urlopen
html = urlopen('http://bit.ly/1Bf5Hft')
HTML(html.read().decode('utf-8'))